<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Imports" data-toc-modified-id="Imports-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Imports</a></span></li><li><span><a href="#Scripted-Data" data-toc-modified-id="Scripted-Data-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Scripted Data</a></span><ul class="toc-item"><li><span><a href="#Creating-the-'train'-dataframe" data-toc-modified-id="Creating-the-'train'-dataframe-2.1"><span class="toc-item-num">2.1&nbsp;&nbsp;</span>Creating the 'train' dataframe</a></span></li></ul></li><li><span><a href="#Original-Data" data-toc-modified-id="Original-Data-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Original Data</a></span><ul class="toc-item"><li><span><a href="#DataLoader" data-toc-modified-id="DataLoader-3.1"><span class="toc-item-num">3.1&nbsp;&nbsp;</span>DataLoader</a></span></li><li><span><a href="#Creating-and-pickling-instance-weight-matrix" data-toc-modified-id="Creating-and-pickling-instance-weight-matrix-3.2"><span class="toc-item-num">3.2&nbsp;&nbsp;</span>Creating and pickling instance weight matrix</a></span></li><li><span><a href="#Miscellaneous-train/test-functions" data-toc-modified-id="Miscellaneous-train/test-functions-3.3"><span class="toc-item-num">3.3&nbsp;&nbsp;</span>Miscellaneous train/test functions</a></span><ul class="toc-item"><li><span><a href="#Cuda-enable" data-toc-modified-id="Cuda-enable-3.3.1"><span class="toc-item-num">3.3.1&nbsp;&nbsp;</span>Cuda-enable</a></span></li><li><span><a href="#Tackling-missing-labels-using-a-mask" data-toc-modified-id="Tackling-missing-labels-using-a-mask-3.3.2"><span class="toc-item-num">3.3.2&nbsp;&nbsp;</span>Tackling missing labels using a mask</a></span></li><li><span><a href="#Linear-Learning-Rate-scheduler" data-toc-modified-id="Linear-Learning-Rate-scheduler-3.3.3"><span class="toc-item-num">3.3.3&nbsp;&nbsp;</span>Linear Learning-Rate scheduler</a></span></li><li><span><a href="#Euclidean-Norm-for-weight-matrices" data-toc-modified-id="Euclidean-Norm-for-weight-matrices-3.3.4"><span class="toc-item-num">3.3.4&nbsp;&nbsp;</span>Euclidean Norm for weight matrices</a></span></li><li><span><a href="#Accuracy-(Precision,-Recall,-F1,-Support,-Balanced-Accuracy)-metrics" data-toc-modified-id="Accuracy-(Precision,-Recall,-F1,-Support,-Balanced-Accuracy)-metrics-3.3.5"><span class="toc-item-num">3.3.5&nbsp;&nbsp;</span>Accuracy (Precision, Recall, F1, Support, Balanced Accuracy) metrics</a></span></li><li><span><a href="#Numpy-Inference" data-toc-modified-id="Numpy-Inference-3.3.6"><span class="toc-item-num">3.3.6&nbsp;&nbsp;</span>Numpy Inference</a></span></li><li><span><a href="#K-Fold-cross-validation-Train-Function" data-toc-modified-id="K-Fold-cross-validation-Train-Function-3.3.7"><span class="toc-item-num">3.3.7&nbsp;&nbsp;</span>K-Fold cross validation Train Function</a></span></li></ul></li></ul></li><li><span><a href="#Multi-Class-Classifier:-MLP2H-Learning" data-toc-modified-id="Multi-Class-Classifier:-MLP2H-Learning-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Multi Class Classifier: MLP2H Learning</a></span><ul class="toc-item"><li><span><a href="#Global-Hyperparameter-variables" data-toc-modified-id="Global-Hyperparameter-variables-4.1"><span class="toc-item-num">4.1&nbsp;&nbsp;</span>Global Hyperparameter variables</a></span></li><li><span><a href="#Using-Multi-Layer-Perceptron-(2-Hidden-Layers)" data-toc-modified-id="Using-Multi-Layer-Perceptron-(2-Hidden-Layers)-4.2"><span class="toc-item-num">4.2&nbsp;&nbsp;</span>Using Multi-Layer Perceptron (2 Hidden Layers)</a></span></li><li><span><a href="#Single-Class-Classifier:-Train-on-scripted,-test-on-user" data-toc-modified-id="Single-Class-Classifier:-Train-on-scripted,-test-on-user-4.3"><span class="toc-item-num">4.3&nbsp;&nbsp;</span>Single Class Classifier: Train on scripted, test on user</a></span></li></ul></li></ul></div>

# Imports

In [41]:
# Required imports
import datetime
import os
import numpy as np
import pandas as pd
import gzip
import glob
import pickle
import copy
import math
import csv
from io import StringIO
import importlib.machinery

from sklearn.metrics import accuracy_score,confusion_matrix,balanced_accuracy_score
from sklearn.metrics import precision_recall_fscore_support,classification_report
#from sklearn.metrics import multilabel_confusion_matrix # Only available in dev .21

# Need Pytorch for multilabel classifications
import torch
from torch.autograd import Variable as V
from torch import nn,optim
import torch.nn.functional as F
import torch.utils.data as utils
#import skorch [Scikit-learn wrapper around Pytorch so allowing for K-fold cross-validation]
random_state=10
np.random.seed(random_state)

from utils import cm,remove_outliers

# Scripted Data

## Creating the 'train' dataframe

In [2]:
# Data location and sample user
scripted_data_folder='dataset/scripted_data/featurized_data_csvs_with_label_1Second/*'
data_1s=glob.glob(scripted_data_folder)
sample_1s=data_1s[0]

In [3]:
sample_df=pd.read_csv(sample_1s)
original_shape=sample_df.shape

# Removing unneeded columns-Location based, Phone measurements based, discrete data
remove_feat_cols=['Unnamed: 0',
             'timestamp',
             'location:num_valid_updates',
             'location:log_latitude_range',
             'location:log_longitude_range',
             'location:min_altitude',
             'location:max_altitude',
             'location:min_speed',
             'location:max_speed',
             'location:best_horizontal_accuracy',
             'location:best_vertical_accuracy',
             'location:diameter',
             'location:log_diameter',
             'location_quick_features:std_lat',
             'location_quick_features:std_long',
             'location_quick_features:lat_change',
             'location_quick_features:long_change',
             'location_quick_features:mean_abs_lat_deriv',
             'location_quick_features:mean_abs_long_deriv',
             'lf_measurements:light',
             'lf_measurements:pressure',
             'lf_measurements:proximity_cm',
             'lf_measurements:proximity',
             'lf_measurements:relative_humidity',
             'lf_measurements:battery_level',
             'lf_measurements:screen_brightness',
             'lf_measurements:temperature_ambient',
             'discrete:app_state:is_active',
             'discrete:app_state:is_inactive',
             'discrete:app_state:is_background',
             'discrete:app_state:missing',
             'discrete:battery_plugged:is_ac',
             'discrete:battery_plugged:is_usb',
             'discrete:battery_plugged:is_wireless',
             'discrete:battery_plugged:missing',
             'discrete:battery_state:is_unknown',
             'discrete:battery_state:is_unplugged',
             'discrete:battery_state:is_not_charging',
             'discrete:battery_state:is_discharging',
             'discrete:battery_state:is_charging',
             'discrete:battery_state:is_full',
             'discrete:battery_state:missing',
             'discrete:on_the_phone:is_False',
             'discrete:on_the_phone:is_True',
             'discrete:on_the_phone:missing',
             'discrete:ringer_mode:is_normal',
             'discrete:ringer_mode:is_silent_no_vibrate',
             'discrete:ringer_mode:is_silent_with_vibrate',
             'discrete:ringer_mode:missing',
             'discrete:wifi_status:is_not_reachable',
             'discrete:wifi_status:is_reachable_via_wifi',
             'discrete:wifi_status:is_reachable_via_wwan',
             'discrete:wifi_status:missing',
             'discrete:time_of_day:between0and6',
             'discrete:time_of_day:between3and9',
             'discrete:time_of_day:between6and12',
             'discrete:time_of_day:between9and15',
             'discrete:time_of_day:between12and18',
             'discrete:time_of_day:between15and21',
             'discrete:time_of_day:between18and24',
             'discrete:time_of_day:between21and3',
             'mfcc_0',
             'mfcc_1',
             'mfcc_2',
             'mfcc_3',
             'mfcc_4',
             'mfcc_5',
             'mfcc_6',
             'mfcc_7',
             'mfcc_8',
             'mfcc_9',
             'mfcc_10',
             'mfcc_11',
             'mfcc_12',
             'mfcc_13',
             'mfcc_14',
             'mfcc_15',
             'mfcc_16',
             'mfcc_17',
             'mfcc_18',
             'mfcc_19',
             'mfcc_20',
             'mfcc_21',
             'mfcc_22',
             'mfcc_23',
             'mfcc_24',
             'mfcc_25']

remove_label_cols=['Assigned Prioception',
             'Assigned Prioception - Except Phone in Hand',
             'Bathroom',
             'Coughing',
             'Jogging',
             'Jumping',
             'Laying Down (action)',
             'Lying Down',
             'Phone in Bag',
             'Phone in Hand',
             'Phone in Pocket',
             'Phone in Table, Facing Down',
             'Phone in Table, Facing Up',
             'Running',
             'Sitting',
             'Sitting Down (action)',
             'Sitting Up (action)',
             'Sleeping',
             'Sneezing',
             'Stairs - Going Down',
             'Stairs - Going Up',
             'Standing',
             'Standing up (action)',
             'Talking On Phone',
             'Trembling',
             'Typing',
             'Walking',
             'Walking, Phone in Pocket',
             'Walking, Phone in Hand',
             'Walking, Phone in Bag',
             'Toilet, Phone in Pocket',
             'Exercising, Phone in Pocket',
             'Laying Down, Phone on Table']

## Map(important_labels--> Scripted labels in dataset)
# Running--> Running
# Lying_down--> Lying Down
# Sitting--> Sitting
# FIX_walking--> Walking
# Sleeping--> Sleeping
# Phone_in_pocket--> Phone in Pocket
# Talking--> Talking On Phone
# Toilet--> Bathroom
# OR_standing--> Standing
# Phone_in_hand--> Phone in Hand
# Phone_in_bag--> Phone in Bag
# Phone_on_table--> Phone in Table, Facing Down AND Phone in Table, Facing Up
useful_labels={'FIX_running':['Running'],
              'LYING_DOWN':['Lying Down'],
              'SITTING':['Sitting'],
              'FIX_walking':['Walking'],
              'SLEEPING':['Sleeping'],
              'PHONE_IN_POCKET':['Phone in Pocket'],
              'TALKING':['Talking On Phone'],
              'TOILET':['Bathroom'],
              'OR_standing':['Standing'],
              'PHONE_IN_HAND':['Phone in Hand'],
              'PHONE_IN_BAG':['Phone in Bag'],
              'PHONE_ON_TABLE':['Phone in Table, Facing Down','Phone in Table, Facing Up']}

## Labels not in merged_labels but present in merged_labels_with_contexts
# Walking, Phone in Pocket
# Walking, Phone in Hand
# Walking, Phone in Bag
# Toilet, Phone in Pocket
# Exercising, Phone in Pocket
# Laying Down, Phone on Table'

for col in remove_feat_cols:
    sample_df.drop(col,axis=1,inplace=True)
final_shape=sample_df.shape

print("Original df shape:{} --> Final df shape:{}".format(original_shape,final_shape))

Original df shape:(4489, 226) --> Final df shape:(4489, 139)


In [4]:
# No contexts
# Features 0-174, 200- 225
# Labels 175- 199

# Contexts
# Features 0-174, 202-227
# Labels 175-201,228-233

In [5]:
# Returns a standardized (0 mean, 1 variance) for a dataframe
def standardize_df(user_df):
    data=user_df.values.astype(float)
    columns=user_df.columns
    mean=np.nanmean(data,axis=0).reshape((1,-1))# Ignores NaNs while finding the mean across rows
    standard_dev=np.nanstd(data,axis=0) # Ignores NaNs while finding the standard deviation across rows
    standard_dev_nonzero=np.where(standard_dev>0,standard_dev,1.).reshape((1,-1)) # Div zero
    
    X=(data-mean)/standard_dev_nonzero
    return pd.DataFrame(data=X,columns=columns)

def scripted_cleaner(glob_path,important_labels_dict,remove_features):
    mapped_labels=[item for sublist in important_labels_dict.values() for item in sublist]
    concat_df=pd.DataFrame()
    
    for g in glob_path: # For csv data in glob_path
        
        fname=g.split('/')[-1].split('.')[0]
        print("FILE: {}".format(fname))
        if fname.endswith('_with_contexts'):
            user_df=pd.read_csv(g)
            user_df_features=user_df.iloc[:,:175]
            user_df_labels=user_df.iloc[:,175:202]
            
            for col in remove_features:
                user_df_features.drop(col,axis=1,inplace=True,errors='ignore') # And ignore if col isn't present
        
        else:
            user_df=pd.read_csv(g)
            user_df_features=user_df.iloc[:,:175]
            user_df_labels=user_df.iloc[:,175:202]
            
            for col in remove_features:
                user_df_features.drop(col,axis=1,inplace=True,errors='ignore')
                
        user_df_features=standardize_df(user_df_features) # Standardize
        user_df_labels=user_df_labels[mapped_labels] # Dataframe of important labels
        user_df=pd.concat([user_df_features,user_df_labels],axis=1) # Stack the features,labels together
        concat_df=pd.concat([concat_df,user_df],ignore_index=True,axis=0) # Concatenating all user dataframes
        concat_df.fillna(value=0,inplace=True)
    # Concat_df=Data concatenated from multiple users containing standardized features, important labels and zero-impute
    return concat_df

In [6]:
scripted_df=scripted_cleaner(glob_path=data_1s,
                             important_labels_dict=useful_labels,
                             remove_features=remove_feat_cols)
scripted_df=scripted_df[scripted_df.columns.drop(list(scripted_df.filter(regex='proc_magnet')))]
with open('dataset/scripted_data/scripted_dataset.pkl','wb') as f:
    pickle.dump(scripted_df,f)

FILE: with_audio_UUID_0111_merged_labels
FILE: with_audio_UUID_0048_merged_labels_with_contexts
FILE: with_audio_UUID_0143_merged_labels
FILE: with_audio_UUID_0039_merged_labels_with_contexts
FILE: with_audio_UUID_0071_merged_labels_with_contexts
FILE: with_audio_UUID_0145_merged_labels
FILE: with_audio_UUID_0072_merged_labels_with_contexts
FILE: with_audio_UUID_0130_merged_labels
FILE: with_audio_UUID_0056_merged_labels_with_contexts
FILE: with_audio_UUID_0101_merged_labels
FILE: with_audio_UUID_0139_merged_labels
FILE: with_audio_UUID_0083_merged_labels_with_contexts
FILE: with_audio_UUID_0055_merged_labels_with_contexts
FILE: with_audio_UUID_0115_merged_labels
FILE: with_audio_UUID_0142_merged_labels
FILE: with_audio_UUID_0128_merged_labels
FILE: with_audio_UUID_0113_merged_labels
FILE: with_audio_UUID_0061_merged_labels_with_contexts
FILE: with_audio_UUID_0116_merged_labels
FILE: with_audio_UUID_0077_merged_labels_with_contexts
FILE: with_audio_UUID_0079_merged_labels_with_contexts

# Original Data

## DataLoader

In [7]:
# Dataset parsers for header/ body for CSVs
def parse_header_of_csv(csv_str):
    # Isolate the headline columns:
    headline = csv_str[:csv_str.index('\n')];
    columns = headline.split(',');

    # The first column should be timestamp:
    assert columns[0] == 'timestamp';
    # The last column should be label_source:
    assert columns[-1] == 'label_source';
    
    # Search for the column of the first label:
    for (ci,col) in enumerate(columns):
        if col.startswith('label:'):
            first_label_ind = ci;
            break;
        pass;

    # Feature columns come after timestamp and before the labels:
    feature_names = columns[1:first_label_ind];
    # Then come the labels, till the one-before-last column:
    label_names = columns[first_label_ind:-1];
    for (li,label) in enumerate(label_names):
        # In the CSV the label names appear with prefix 'label:', but we don't need it after reading the data:
        assert label.startswith('label:');
        label_names[li] = label.replace('label:','');
        pass;
    
    return (feature_names,label_names);

def parse_body_of_csv(csv_str,n_features):
    # Read the entire CSV body into a single numeric matrix:
    full_table = np.loadtxt(StringIO(csv_str),delimiter=',',skiprows=1);
    
    # Timestamp is the primary key for the records (examples):
    timestamps = full_table[:,0].astype(int);
    
    # Read the sensor features:
    X = full_table[:,1:(n_features+1)];
    
    # Read the binary label values, and the 'missing label' indicators:
    trinary_labels_mat = full_table[:,(n_features+1):-1]; # This should have values of either 0., 1. or NaN
    M = np.isnan(trinary_labels_mat); # M is the missing label matrix
    
    #print("M matrix shape:",M.shape)
    #print("Matrix: ",np.argwhere(M))
    trinary_labels_mat[M]=-1 # Replace NaNs with -1.0 for which we then apply a mask
    unique,counts=np.unique(trinary_labels_mat,return_counts=True)
    print(*zip(unique,counts)) 
    
#     Y = np.where(M,0,trinary_labels_mat) > 0.; # Y is the label matrix
    
    return (X,trinary_labels_mat,M,timestamps);

def read_user_data(directory):
    print('Reading {}'.format(directory.split("/")[-1]))

    # Read the entire csv file of the user:
    with gzip.open(directory,'rb') as fid:
        csv_str = fid.read();
        csv_str = csv_str.decode("utf-8")
        pass;

    (feature_names,label_names) = parse_header_of_csv(csv_str);
    n_features = len(feature_names);
    (X,Y,M,timestamps) = parse_body_of_csv(csv_str,n_features);

    return (X,Y,M,timestamps,feature_names,label_names);

In [8]:
# Get a summary of the sensor feature
'''
# Summarize features as we are only using phone_acc,phone_gyro,phone_mag,phone_loc,phone_audio,
# phone_app,phone_battery,phone_use,phone_callstat,phone_wifi,phone_lf,phone_time
# We are ignoring the use of the smartwatch features. There are definitely features that will be used
# much more (e.g. than the phone_callstat) but we'll leave that up to the ML algorithm.
'''
# Get a summary of the sensor feature along with the original label that was used
def summarize_features_worig(feature_list):
    summary_feature_list=np.empty((len(feature_list),2),dtype=object)
    
    for (ind,feature) in enumerate(feature_list):
        if feature.startswith('raw_acc'):
            summary_feature_list[ind,0]='phone_acc'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('proc_gyro'):
            summary_feature_list[ind,0]='phone_gyro'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('raw_magnet'):
            summary_feature_list[ind,0]='phone_mag'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('watch_acc'):
            summary_feature_list[ind,0]='watch_acc'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('watch_heading'):
            summary_feature_list[ind,0]='watch_dir'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('location'):
            summary_feature_list[ind,0]='phone_loc'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('audio'):
            summary_feature_list[ind,0]='phone_audio'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('discrete:app_state'):
            summary_feature_list[ind,0]='phone_app'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('discrete:battery'):
            summary_feature_list[ind,0]='phone_battery'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('discrete:on'):
            summary_feature_list[ind,0]='phone_use'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('discrete:ringer'):
            summary_feature_list[ind,0]='phone_callstat'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('discrete:wifi'):
            summary_feature_list[ind,0]='phone_wifi'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('lf'):
            summary_feature_list[ind,0]='phone_lf'
            summary_feature_list[ind,1]=feature
            
        if feature.startswith('discrete:time'):
            summary_feature_list[ind,0]='phone_time'
            summary_feature_list[ind,1]=feature

    return summary_feature_list

In [9]:
# Choosing sensor labels
'''
Summary sensor choices are: phone_acc,phone_gyro,phone_mag,watch_acc,watch_dir,phone_loc,phone_audio,
phone_app,phone_battery,phone_use,phone_callstat,phone_wifi,phone_lf,phone_time
In this project, we aren't using watch_acc,watch_dir (no smartwatch)
'''

def choose_sensors_longnames(X_train,used_sensors,long_featurenames):
    
    used_sensor_feature_names=np.zeros(len(long_featurenames),dtype=bool)
    used_feature_actualnames=np.zeros(len(long_featurenames),dtype=bool)
    # Creates a zero boolean vector of all possible feature names
    summary_features=long_featurenames[:,0]
    all_complete_features=long_featurenames[:,-1]
    
    for s in used_sensors:
        similar=(s==summary_features)
        
        #used_complete_features=(all_complete_features[similar.astype(int)])
       
        used_sensor_feature_names=np.logical_or(used_sensor_feature_names,similar)
        used_feature_actualnames=np.logical_or(used_feature_actualnames,similar)
    
    X_train=X_train[:,used_sensor_feature_names]
    long_names=all_complete_features[used_feature_actualnames]
    return X_train,long_names

In [10]:
# Sensor Types, Label Possibilities variables
sensor_types=['phone_acc','phone_gyro','phone_mag','phone_loc','phone_audio',
'phone_app','phone_battery','phone_use','phone_callstat','phone_wifi','phone_lf',
'phone_time']
label_possibilities=['LOC_home','OR_indoors','PHONE_ON_TABLE','SITTING','WITH_FRIENDS',
 'LYING_DOWN','SLEEPING','WATCHING_TV','EATING','PHONE_IN_POCKET',
 'TALKING','DRIVE_-_I_M_A_PASSENGER','OR_standing','IN_A_CAR',
 'OR_exercise','AT_THE_GYM','SINGING','FIX_walking','OR_outside',
 'SHOPPING','AT_SCHOOL','BATHING_-_SHOWER','DRESSING','DRINKING__ALCOHOL_',
 'PHONE_IN_HAND','FIX_restaurant','IN_CLASS','PHONE_IN_BAG','IN_A_MEETING',
 'TOILET','COOKING','ELEVATOR','FIX_running','BICYCLING','LAB_WORK',
 'LOC_main_workplace','ON_A_BUS','DRIVE_-_I_M_THE_DRIVER','STROLLING',
 'CLEANING','DOING_LAUNDRY','WASHING_DISHES','SURFING_THE_INTERNET',
 'AT_A_PARTY','AT_A_BAR','LOC_beach','COMPUTER_WORK','GROOMING','STAIRS_-_GOING_UP',
 'STAIRS_-_GOING_DOWN','WITH_CO-WORKERS']

In [11]:
# Reading sample data
prefix='dataset/Extrasensory_uuid_fl_uTAR'
user_sample='0A986513-7828-4D53-AA1F-E02D6DF9561B.features_labels'
sample_loc='{}/{}.csv.gz'.format(prefix,user_sample)
x_user,y_user,missedlabel_user,tstamp_user,featurename_user,labelname_user=read_user_data(sample_loc)

feature_names_woriginallabels=summarize_features_worig(featurename_user)
    
x_train_chosen,feature_long_names=choose_sensors_longnames(x_user,sensor_types,feature_names_woriginallabels)

subject_x_df=pd.DataFrame(x_train_chosen,columns=feature_long_names)
subject_y_df=pd.DataFrame(y_user,columns=labelname_user)

for col in remove_feat_cols:
    subject_x_df.drop(col,axis=1,inplace=True,errors='ignore') # Drop some columns

subject_x_df=subject_x_df[subject_x_df.columns.drop(list(subject_x_df.filter(regex='audio')))]

subject_x_df=standardize_df(subject_x_df) # Standardize

Reading 0A986513-7828-4D53-AA1F-E02D6DF9561B.features_labels.csv.gz
(-1.0, 129722) (0.0, 59014) (1.0, 13224)


## Creating and pickling instance weight matrix

In [29]:
# Creating an instance weight matrix for the training labels
def instance_weight_matrix(y_train):
    instance_weights=np.zeros_like(y_train)
    for l in range(1):
        temp_column=y_train[:,l]
        count_neg=0
        count_0=0
        count_1=0
        for i in range(len(temp_column)): # n^2 bincount doesn't work with arrays consisting of negative numbers
            if (temp_column[i]==-1):
                count_neg+=1
            elif (temp_column[i]==0):
                count_0+=1
            elif (temp_column[i]==1):
                count_1+=1
            else:
                raise ValueError("Bad Loop")
#         print(l,count_0,count_1)
        if(count_0!=0):
            weight_0=float((count_0+count_1)/count_0)
        else:
            weight_0=0.
        if(count_1!=0):
            weight_1=float((count_0+count_1)/count_1)
        else:
            weight_1=0.
        if(weight_0+weight_1==0.):
            weight_0=1.
            weight_1=1.
        else:
            weight_0=weight_0/(weight_0+weight_1)
            weight_1=weight_1/(weight_0+weight_1)

        for i in range(len(temp_column)):
            if (temp_column[i]==-1):
                instance_weights[i,l]=0.
            elif (temp_column[i]==0):
                instance_weights[i,l]=weight_0
            elif (temp_column[i]==1):
                instance_weights[i,l]=weight_1
    return instance_weights

## Miscellaneous train/test functions

### Cuda-enable

In [13]:
# Simple function to run using GPU when available
def C(structure):
    if torch.cuda.is_available():
        device=torch.device("cuda")
        return structure.to(device)

### Tackling missing labels using a mask

In [14]:
# Create a mask to hide -1 nans before training and then input to a train criterion
def mask(criterion,y_true,y_pred,mask_value=-1.):
    mask=torch.ne(y_true,mask_value).type(torch.cuda.FloatTensor)
    # Cast the ByteTensor from elementwise comparison to a FloatTensor
    return criterion(torch.mul(y_pred,mask),torch.mul(y_true,mask))

### Linear Learning-Rate scheduler

In [15]:
# Linear decreasing LR scheduler
def linear_lr_scheduler(optimizer,epoch):
    """
    LR_init=0.1, LR_final=0.01, n_epochs=40
    Sets the learning rate to the initial LR decayed by 1.04 every epoch"""
    for param_group in optimizer.param_groups:
        lr=param_group['lr']
    m=-3/1300
    c=0.1
    lr=(epoch*m)+c # Linear LR decay based on a set number of epochs
    for param_group in optimizer.param_groups:
        param_group['lr']=lr

### Euclidean Norm for weight matrices

In [16]:
# Adds euclidean regularization to weight matrices
def frobenius_norm(model,loss):
    regularizer_loss=0
    
    for m in model.modules():
        if isinstance(m,nn.Linear): # Linear layer
            frobenius_norm=torch.norm(m.weight,p='fro')
            regularizer_loss+=frobenius_norm # Regularization over the weight matrices for linear layers
    return loss+0.001*regularizer_loss

### Accuracy (Precision, Recall, F1, Support, Balanced Accuracy) metrics

In [36]:
# Function for the required accuracy metrics per fold
def accuracy(fold,target_labels,y_true,y_pred):
    y_true=y_true.detach().numpy()
    y_pred=y_pred.detach().numpy()
    balanced_accuracy_dict={}
    print('*'*20)
    print('For fold {}'.format(fold))
    
    # Balanced accuracy
    for i in range(1):
        true_perlabel=y_true[:,i]
        pred_perlabel=y_pred[:,i]
        initial_shape=true_perlabel.shape
        
        invalid_mask=np.where(true_perlabel==-1.)
        valid_mask=np.where(true_perlabel!=-1.) # Create a mask
        true_perlabel=true_perlabel[valid_mask]
        pred_perlabel=pred_perlabel[valid_mask]
        
        bal_acc=balanced_accuracy_score(y_true=true_perlabel,y_pred=pred_perlabel)
        print('\t Label {}:::-> Balanced Accuracy {}'.format(target_labels[i],round(bal_acc,7)))
#         print('\t\t Initial length {}, Missing mask length {}, Valid mask length {}, Final length {}'
#               .format(initial_shape[0],len(invalid_mask[0]),len(valid_mask[0]),len(true_perlabel)))
        balanced_accuracy_dict[target_labels]=round(bal_acc,5)
    return balanced_accuracy_dict

### Numpy Inference

In [18]:
def I(tensor):
    return tensor.cpu().detach().numpy() # Run on CPU, detach from variable in graph, convert to array

### K-Fold cross validation Train Function

In [37]:
# Train function w/BCE loss, linear LR scheduler, instance weights
def train(model,X,Y,weights,n_epoch,batch_size,lr_init,momentum,fold,label):
    
    optimizer=optim.SGD(model.parameters(),lr=lr_init,momentum=momentum)

    X=V(torch.cuda.FloatTensor(X),requires_grad=True)
    Y=V(torch.cuda.FloatTensor(Y),requires_grad=False)
    weights=V(torch.cuda.FloatTensor(weights),requires_grad=False)
   
    # Cuda-Compatible Model
    model = C(model)
    # Create dataloaders
    # Dataloader creation
    # Wrap weights for instance weight tensor along with data & label tensors s.t.
    # it can be called properly as a dataloader in batches.
    train_dataset=utils.TensorDataset(X,Y,weights)
    train_loader=utils.DataLoader(dataset=train_dataset,batch_size=bs
                                  ,shuffle=False,drop_last=False)

    for epoch in range(n_epoch):
        linear_lr_scheduler(optimizer,epoch)
        for i,data in enumerate(train_loader,0):

            inputs,labels,weights=data
            inputs=V(torch.cuda.FloatTensor(inputs),requires_grad=True)
            labels=V(torch.cuda.FloatTensor(labels),requires_grad=False)
            weights=V(torch.cuda.FloatTensor(weights),requires_grad=False)

            criterion=C(nn.BCEWithLogitsLoss(weight=weights))
            optimizer.zero_grad()   
            sum_total=0

            outputs=model(inputs)

            # Zero gradients, backward pass, weight update
#             loss=criterion(outputs,labels) 
            loss=mask(criterion=criterion,y_true=labels,y_pred=outputs,mask_value=-1)
            loss=frobenius_norm(model,loss)
            loss.backward()
            optimizer.step()

            sum_total+=loss.item()
            for param_group in optimizer.param_groups:
                epoch_lr=param_group['lr']

            print("Epoch {}::Minibatch {}::LR {} --> Loss {}".format(epoch+1,i+1,epoch_lr,sum_total/bs))
            sum_total=0.
        
    
    print("Training finished, Prediction")
    
    model.eval() # Evaluation model
    
    y_pred=torch.sigmoid(model(X))>=0.5
    fold_train_dict=accuracy(fold,label,Y.cpu(),y_pred.cpu())
    
    
    return fold_train_dict,model

# Multi Class Classifier: MLP2H Learning

Learning on scripted data and testing on  actual users

## Global Hyperparameter variables

In [22]:
# Defining sizes for neural networks and other global hyperparameters
input_size=83
hidden_size=16
output_size=1
n_epoch=40
bs=300
lr_init=0.1
momentum=0.5
print('Input Size {}, Output Size {}'.format(input_size,output_size))

Input Size 83, Output Size 1


## Using Multi-Layer Perceptron (2 Hidden Layers)

In [23]:
class MLP_2H(nn.Module):
    def __init__(self):
        super(MLP_2H,self).__init__()
        self.hidden0=nn.Sequential(
            nn.Linear(input_size,hidden_size),
            nn.LeakyReLU(negative_slope=0.1)
        )
        self.hidden1=nn.Sequential(
            nn.Linear(hidden_size,hidden_size),
            nn.LeakyReLU(negative_slope=0.1)
        )
        self.out=nn.Sequential(
            nn.Linear(hidden_size,output_size)
        )
        
    def forward(self,x):
        x = self.hidden0(x)
        x = self.hidden1(x)
        return self.out(x)
    
# Train for MLP-2 Hidden
model=MLP_2H()
print(model)

MLP_2H(
  (hidden0): Sequential(
    (0): Linear(in_features=83, out_features=16, bias=True)
    (1): LeakyReLU(negative_slope=0.1)
  )
  (hidden1): Sequential(
    (0): Linear(in_features=16, out_features=16, bias=True)
    (1): LeakyReLU(negative_slope=0.1)
  )
  (out): Sequential(
    (0): Linear(in_features=16, out_features=1, bias=True)
  )
)


## Single Class Classifier: Train on scripted, test on user

In [ ]:
scripted_pickled_data='dataset/scripted_data/scripted_dataset.pkl'
with open(scripted_pickled_data,'rb') as f:      
    all_scripted=pickle.load(f)

dataset_length=len(all_scripted)
# 114 Running
# 115 Lying Down
# 116 Sitting
# 117 Walking
# 118 Sleeping
# 119 Phone in Pocket
# 120 Talking On Phone
# 121 Bathroom
# 122 Standing
# 123 Phone in Hand
# 124 Phone in Bag
# 125 Phone in Table, Facing Down
# 126 Phone in Table, Facing Up

for label in useful_labels.keys():
    print("*"*20,"WORKING ON LABEL: ",label,"*"*20)
    x_scripted=all_scripted.iloc[:,:83].values
    if label=='Phone_on_table':
        temp_y=all_scripted[useful_labels[label]] # Returns two columns (Phone on table:facing down, facing up)
        y_scripted=temp_y.max(axis=1).values.reshape(dataset_length,1) # Combinining both into a single column
    else:
        y_scripted=all_scripted[useful_labels[label]].values.reshape(dataset_length,1)
    weights=instance_weight_matrix(y_scripted)
    
    
    model=MLP_2H() # Instantiate a new MLP2H model
    fold_train_dict,trained_model=train(model=model,
                         X=x_scripted,
                         Y=y_scripted,
                         weights=weights,
                         n_epoch=n_epoch,
                         batch_size=bs,
                         lr_init=lr_init,
                         momentum=momentum,
                         fold="-1",
                         label=label)
    print(fold_train_dict)
    given_y_all=[]
    generated_y_all=[]
    for g in glob.glob(prefix+"/*"):
        fname=g.split('/')[-1].split('.')[0]
        x_user,y_user,missedlabel_user,tstamp_user,featurename_user,labelname_user=read_user_data(g)

        feature_names_woriginallabels=summarize_features_worig(featurename_user)

        x_train_chosen,feature_long_names=choose_sensors_longnames(x_user,sensor_types,feature_names_woriginallabels)

        subject_x_df=pd.DataFrame(x_train_chosen,columns=feature_long_names)
        subject_y_df=pd.DataFrame(y_user,columns=labelname_user)

        for col in remove_feat_cols:
            subject_x_df.drop(col,axis=1,inplace=True,errors='ignore') # Drop some columns

        subject_x_df=subject_x_df[subject_x_df.columns.drop(list(subject_x_df.filter(regex='audio')))]

        subject_x_df=standardize_df(subject_x_df) # Standardize
        subject_y_df=subject_y_df[label].values
        
        trained_model.eval() # Evaluation of trained model
        subject_x=V(torch.cuda.FloatTensor(subject_x_df.values),requires_grad=False)
        
        Y_test_pred=torch.sigmoid(trained_model(subject_x))>=0.5
        Y_test_pred=Y_test_pred.cpu().detach().numpy()
        
        save_fname='dataset/scripted_y_data/'+fname+'_'+label+'.csv'
        with open(save_fname, 'wt') as f:
            csv_writer = csv.writer(f)
 
            for row in Y_test_pred:
                csv_writer.writerow(row)
        f.close()
        given_y_all.extend(subject_y_df)
        generated_y_all.extend(Y_test_pred)
    
    given_y_all=np.asarray(given_y_all)
    generated_y_all=np.asarray(generated_y_all)
    count_change=0
    count_new_neg=0
    count_new_pos=0
    for i in range(len(given_y_all)):
        if(given_y_all[i]==0.0 and generated_y_all[i]==1.0):
            count_change+=1
        if(given_y_all[i]==1.0 and generated_y_all[i]==0.0):
            count_change+=1
        if(given_y_all[i]==-1.0 and generated_y_all[i]==0.0):
            count_new_neg+=1
        if(given_y_all[i]==-1.0 and generated_y_all[i]==1.0):
            count_new_pos+=1
    print("After evaluating on extrasensory_data (size {}): y_value change is {}, nan to neg change is {} nan to pos change is {}. ".format(len(generated_y_all),count_change,count_new_neg,count_new_pos))

******************** WORKING ON LABEL:  FIX_running ********************
Epoch 1::Minibatch 1::LR 0.1 --> Loss 3.915340018769105e-05
Epoch 1::Minibatch 2::LR 0.1 --> Loss 3.897189473112424e-05
Epoch 1::Minibatch 3::LR 0.1 --> Loss 3.941417361299197e-05
Epoch 1::Minibatch 4::LR 0.1 --> Loss 4.1453974942366284e-05
Epoch 1::Minibatch 5::LR 0.1 --> Loss 3.918195764223734e-05
Epoch 1::Minibatch 6::LR 0.1 --> Loss 3.951239089171092e-05
Epoch 1::Minibatch 7::LR 0.1 --> Loss 3.930837536851565e-05
Epoch 1::Minibatch 8::LR 0.1 --> Loss 3.9952040339509646e-05
Epoch 1::Minibatch 9::LR 0.1 --> Loss 4.047688407202562e-05
Epoch 1::Minibatch 10::LR 0.1 --> Loss 3.9654274781545e-05
Epoch 1::Minibatch 11::LR 0.1 --> Loss 3.940291702747345e-05
Epoch 1::Minibatch 12::LR 0.1 --> Loss 3.948934997121493e-05
Epoch 1::Minibatch 13::LR 0.1 --> Loss 3.997484842936198e-05
Epoch 1::Minibatch 14::LR 0.1 --> Loss 4.019590094685554e-05
Epoch 1::Minibatch 15::LR 0.1 --> Loss 3.98078840225935e-05
Epoch 1::Minibatch 16:

Epoch 1::Minibatch 159::LR 0.1 --> Loss 4.349477278689544e-05
Epoch 1::Minibatch 160::LR 0.1 --> Loss 4.012166212002436e-05
Epoch 1::Minibatch 161::LR 0.1 --> Loss 3.867326614757379e-05
Epoch 1::Minibatch 162::LR 0.1 --> Loss 4.498229362070561e-05
Epoch 1::Minibatch 163::LR 0.1 --> Loss 4.617847502231598e-05
Epoch 1::Minibatch 164::LR 0.1 --> Loss 4.020682846506437e-05
Epoch 1::Minibatch 165::LR 0.1 --> Loss 4.1499923293789226e-05
Epoch 1::Minibatch 166::LR 0.1 --> Loss 4.391917958855629e-05
Epoch 1::Minibatch 167::LR 0.1 --> Loss 3.92147774497668e-05
Epoch 1::Minibatch 168::LR 0.1 --> Loss 0.00014779288321733474
Epoch 1::Minibatch 169::LR 0.1 --> Loss 4.204891932507356e-05
Epoch 1::Minibatch 170::LR 0.1 --> Loss 4.1338571657737094e-05
Epoch 1::Minibatch 171::LR 0.1 --> Loss 4.4826694453756017e-05
Epoch 1::Minibatch 172::LR 0.1 --> Loss 4.0271257360776266e-05
Epoch 1::Minibatch 173::LR 0.1 --> Loss 3.9238184690475464e-05
Epoch 1::Minibatch 174::LR 0.1 --> Loss 3.8731203724940616e-05
Ep

Epoch 1::Minibatch 321::LR 0.1 --> Loss 4.199877381324768e-05
Epoch 1::Minibatch 322::LR 0.1 --> Loss 4.045570269227028e-05
Epoch 1::Minibatch 323::LR 0.1 --> Loss 3.864855505526066e-05
Epoch 1::Minibatch 324::LR 0.1 --> Loss 4.1507879892985025e-05
Epoch 1::Minibatch 325::LR 0.1 --> Loss 3.7886761128902434e-05
Epoch 1::Minibatch 326::LR 0.1 --> Loss 3.816274305184682e-05
Epoch 1::Minibatch 327::LR 0.1 --> Loss 3.6651790142059324e-05
Epoch 1::Minibatch 328::LR 0.1 --> Loss 3.929936637481054e-05
Epoch 1::Minibatch 329::LR 0.1 --> Loss 5.001219610373179e-05
Epoch 1::Minibatch 330::LR 0.1 --> Loss 4.7333563367525735e-05
Epoch 1::Minibatch 331::LR 0.1 --> Loss 4.207452138264974e-05
Epoch 1::Minibatch 332::LR 0.1 --> Loss 0.00017798125743865968
Epoch 1::Minibatch 333::LR 0.1 --> Loss 3.868270044525464e-05
Epoch 1::Minibatch 334::LR 0.1 --> Loss 4.919925704598427e-05
Epoch 1::Minibatch 335::LR 0.1 --> Loss 3.943956146637599e-05
Epoch 1::Minibatch 336::LR 0.1 --> Loss 4.409139975905418e-05
Epo

Epoch 1::Minibatch 481::LR 0.1 --> Loss 3.708244611819585e-05
Epoch 1::Minibatch 482::LR 0.1 --> Loss 3.739424670735995e-05
Epoch 1::Minibatch 483::LR 0.1 --> Loss 3.940081844727198e-05
Epoch 1::Minibatch 484::LR 0.1 --> Loss 3.478784424563249e-05
Epoch 1::Minibatch 485::LR 0.1 --> Loss 3.444966239233812e-05
Epoch 1::Minibatch 486::LR 0.1 --> Loss 3.5593708356221515e-05
Epoch 1::Minibatch 487::LR 0.1 --> Loss 3.616317175328732e-05
Epoch 1::Minibatch 488::LR 0.1 --> Loss 3.3844485878944395e-05
Epoch 1::Minibatch 489::LR 0.1 --> Loss 3.371721754471461e-05
Epoch 1::Minibatch 490::LR 0.1 --> Loss 3.659871096412341e-05
Epoch 1::Minibatch 491::LR 0.1 --> Loss 4.8031934226552646e-05
Epoch 1::Minibatch 492::LR 0.1 --> Loss 4.723719010750453e-05
Epoch 1::Minibatch 493::LR 0.1 --> Loss 3.9897666623195014e-05
Epoch 1::Minibatch 494::LR 0.1 --> Loss 3.770201777418454e-05
Epoch 1::Minibatch 495::LR 0.1 --> Loss 5.475917831063271e-05
Epoch 1::Minibatch 496::LR 0.1 --> Loss 4.070994754632314e-05
Epoc

Epoch 1::Minibatch 643::LR 0.1 --> Loss 3.4356762965520224e-05
Epoch 1::Minibatch 644::LR 0.1 --> Loss 4.473381054898103e-05
Epoch 1::Minibatch 645::LR 0.1 --> Loss 3.368984597424666e-05
Epoch 1::Minibatch 646::LR 0.1 --> Loss 3.323027864098549e-05
Epoch 1::Minibatch 647::LR 0.1 --> Loss 3.264074213802815e-05
Epoch 1::Minibatch 648::LR 0.1 --> Loss 3.3073816448450087e-05
Epoch 1::Minibatch 649::LR 0.1 --> Loss 3.5612502445777255e-05
Epoch 1::Minibatch 650::LR 0.1 --> Loss 3.980455609659354e-05
Epoch 1::Minibatch 651::LR 0.1 --> Loss 3.181639437874158e-05
Epoch 1::Minibatch 652::LR 0.1 --> Loss 4.897965118288994e-05
Epoch 1::Minibatch 653::LR 0.1 --> Loss 3.646686673164368e-05
Epoch 1::Minibatch 654::LR 0.1 --> Loss 4.123612617452939e-05
Epoch 1::Minibatch 655::LR 0.1 --> Loss 3.237048164010048e-05
Epoch 1::Minibatch 656::LR 0.1 --> Loss 3.5096139957507454e-05
Epoch 1::Minibatch 657::LR 0.1 --> Loss 3.356911242008209e-05
Epoch 1::Minibatch 658::LR 0.1 --> Loss 3.697241966923078e-05
Epoc

...

Epoch 12::Minibatch 1261::LR 0.07461538461538461 --> Loss 9.727374805758397e-06
Epoch 12::Minibatch 1262::LR 0.07461538461538461 --> Loss 9.725437654803197e-06
Epoch 12::Minibatch 1263::LR 0.07461538461538461 --> Loss 9.723443848391375e-06
Epoch 12::Minibatch 1264::LR 0.07461538461538461 --> Loss 9.721225748459498e-06
Epoch 12::Minibatch 1265::LR 0.07461538461538461 --> Loss 9.718926157802344e-06
Epoch 12::Minibatch 1266::LR 0.07461538461538461 --> Loss 9.716783339778583e-06
Epoch 12::Minibatch 1267::LR 0.07461538461538461 --> Loss 9.714688640087842e-06
Epoch 12::Minibatch 1268::LR 0.07461538461538461 --> Loss 9.712423197925091e-06
Epoch 12::Minibatch 1269::LR 0.07461538461538461 --> Loss 9.71010032420357e-06
Epoch 12::Minibatch 1270::LR 0.07461538461538461 --> Loss 9.707948192954063e-06
Epoch 12::Minibatch 1271::LR 0.07461538461538461 --> Loss 9.705849612752596e-06
Epoch 12::Minibatch 1272::LR 0.07461538461538461 --> Loss 9.70358494669199e-06
Epoch 12::Minibatch 1273::LR 0.07461538461

Epoch 12::Minibatch 1381::LR 0.07461538461538461 --> Loss 4.069214997192224e-05
Epoch 12::Minibatch 1382::LR 0.07461538461538461 --> Loss 9.605580319960913e-06
Epoch 12::Minibatch 1383::LR 0.07461538461538461 --> Loss 9.606250872214635e-06
Epoch 12::Minibatch 1384::LR 0.07461538461538461 --> Loss 9.605383966118097e-06
Epoch 12::Minibatch 1385::LR 0.07461538461538461 --> Loss 9.603778986881176e-06
Epoch 12::Minibatch 1386::LR 0.07461538461538461 --> Loss 9.602000936865806e-06
Epoch 12::Minibatch 1387::LR 0.07461538461538461 --> Loss 9.600108023732901e-06
Epoch 12::Minibatch 1388::LR 0.07461538461538461 --> Loss 9.597962101300558e-06
Epoch 12::Minibatch 1389::LR 0.07461538461538461 --> Loss 9.595716061691443e-06
Epoch 12::Minibatch 1390::LR 0.07461538461538461 --> Loss 9.593621362000704e-06
Epoch 12::Minibatch 1391::LR 0.07461538461538461 --> Loss 0.00016518379251162212
Epoch 12::Minibatch 1392::LR 0.07461538461538461 --> Loss 9.614744534095129e-06
Epoch 12::Minibatch 1393::LR 0.07461538

Epoch 13::Minibatch 28::LR 0.07230769230769231 --> Loss 9.76838559533159e-06
Epoch 13::Minibatch 29::LR 0.07230769230769231 --> Loss 9.780824184417725e-06
Epoch 13::Minibatch 30::LR 0.07230769230769231 --> Loss 9.784755141784747e-06
Epoch 13::Minibatch 31::LR 0.07230769230769231 --> Loss 9.784621652215719e-06
Epoch 13::Minibatch 32::LR 0.07230769230769231 --> Loss 9.78244934231043e-06
Epoch 13::Minibatch 33::LR 0.07230769230769231 --> Loss 9.779060880343119e-06
Epoch 13::Minibatch 34::LR 0.07230769230769231 --> Loss 9.77507404362162e-06
Epoch 13::Minibatch 35::LR 0.07230769230769231 --> Loss 9.77098864192764e-06
Epoch 13::Minibatch 36::LR 0.07230769230769231 --> Loss 9.76684115206202e-06
Epoch 13::Minibatch 37::LR 0.07230769230769231 --> Loss 9.762467816472054e-06
Epoch 13::Minibatch 38::LR 0.07230769230769231 --> Loss 9.757992811501027e-06
Epoch 13::Minibatch 39::LR 0.07230769230769231 --> Loss 0.00019376810640096666
Epoch 13::Minibatch 40::LR 0.07230769230769231 --> Loss 4.0376596152

Epoch 13::Minibatch 151::LR 0.07230769230769231 --> Loss 9.738851804286242e-06
Epoch 13::Minibatch 152::LR 0.07230769230769231 --> Loss 9.737346166123947e-06
Epoch 13::Minibatch 153::LR 0.07230769230769231 --> Loss 9.735426089415948e-06
Epoch 13::Minibatch 154::LR 0.07230769230769231 --> Loss 9.733321300397317e-06
Epoch 13::Minibatch 155::LR 0.07230769230769231 --> Loss 9.731284808367491e-06
Epoch 13::Minibatch 156::LR 0.07230769230769231 --> Loss 9.72926306227843e-06
Epoch 13::Minibatch 157::LR 0.07230769230769231 --> Loss 9.72708376745383e-06
Epoch 13::Minibatch 158::LR 0.07230769230769231 --> Loss 9.724854025989771e-06
Epoch 13::Minibatch 159::LR 0.07230769230769231 --> Loss 9.722754669686158e-06
Epoch 13::Minibatch 160::LR 0.07230769230769231 --> Loss 9.72070110340913e-06
Epoch 13::Minibatch 161::LR 0.07230769230769231 --> Loss 9.71851171925664e-06
Epoch 13::Minibatch 162::LR 0.07230769230769231 --> Loss 9.418678159515063e-05
Epoch 13::Minibatch 163::LR 0.07230769230769231 --> Loss

Epoch 13::Minibatch 267::LR 0.07230769230769231 --> Loss 9.698229841887951e-06
Epoch 13::Minibatch 268::LR 0.07230769230769231 --> Loss 9.696159201363723e-06
Epoch 13::Minibatch 269::LR 0.07230769230769231 --> Loss 9.693959727883338e-06
Epoch 13::Minibatch 270::LR 0.07230769230769231 --> Loss 8.668357506394386e-05
Epoch 13::Minibatch 271::LR 0.07230769230769231 --> Loss 9.699939594914516e-06
Epoch 13::Minibatch 272::LR 0.07230769230769231 --> Loss 9.703329609086115e-06
Epoch 13::Minibatch 273::LR 0.07230769230769231 --> Loss 9.702743651966254e-06
Epoch 13::Minibatch 274::LR 0.07230769230769231 --> Loss 9.700190275907516e-06
Epoch 13::Minibatch 275::LR 0.07230769230769231 --> Loss 9.697736240923404e-06
Epoch 13::Minibatch 276::LR 0.07230769230769231 --> Loss 9.695902311553558e-06
Epoch 13::Minibatch 277::LR 0.07230769230769231 --> Loss 9.693819253395e-06
Epoch 13::Minibatch 278::LR 0.07230769230769231 --> Loss 9.69163685416182e-06
Epoch 13::Minibatch 279::LR 0.07230769230769231 --> Loss